In [1]:
import argparse
import pickle as pk

import torch
# For machine learning tools and evaluation
from sklearn.metrics import accuracy_score
# Transformer library
from transformers import AutoTokenizer, AutoModelForCausalLM
from transformers import Trainer, TrainingArguments
import evaluate

data_dir = "./data/"
device_name = "cuda" if torch.cuda.is_available() else "cpu"

/home/aww66/.conda/envs/huggingface/lib/python3.9/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


# load data

In [4]:
subreddit = "Christianity"
month = '2016-12'

from datasets import load_dataset, Dataset

usecols=['year-month', 'timestamp', 'text', 'speaker']
comments_df = pk.load(open(data_dir + f"{subreddit}-comments.pk", "rb"))
comments_df = comments_df[usecols]

monthly_comments_df = comments_df[comments_df['year-month'] == month]
monthly_comments = Dataset.from_pandas(monthly_comments_df)

In [5]:
monthly_comments = monthly_comments.train_test_split(test_size=0.2)

In [6]:
monthly_comments

DatasetDict({
    train: Dataset({
        features: ['year-month', 'timestamp', 'text', 'speaker', 'id'],
        num_rows: 44703
    })
    test: Dataset({
        features: ['year-month', 'timestamp', 'text', 'speaker', 'id'],
        num_rows: 11176
    })
})

# process data
https://huggingface.co/docs/transformers/tasks/language_modeling

In [7]:
model_name = 'distilgpt2'
tokenizer = AutoTokenizer.from_pretrained(model_name)

In [8]:
def preprocess_function(examples):
    return tokenizer(examples["text"], truncation=True)

In [9]:
tokenized_monthly_comments = monthly_comments.map(
    preprocess_function,
    batched=True,
    num_proc=4,
    remove_columns = monthly_comments["train"].column_names,
)

#1:   0%|                                                                                                                                                                                                              | 0/12 [00:00<?, ?ba/s]

#2:   0%|                                                                                                                                                                                                              | 0/12 [00:00<?, ?ba/s]


#1:   8%|████████████████▌                                                                                                                                                                                     | 1/12 [00:01<00:17,  1.56s/ba]

#2:   8%|████████████████▌                                                                                                                                                                                     | 1/12 [00:01<00:16,  1.49s/ba]


#1:  17%|█████████████████████████████

#0: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 12/12 [00:14<00:00,  1.19s/ba]

#1:  92%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▌                | 11/12 [00:14<00:01,  1.25s/ba]

#1: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 12/12 [00:14<00:00,  1.19s/ba]


#2: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 12/12 [00:13<00:00,  1.17s/ba]



#1:   0%|                            

In [10]:
block_size = 128


def group_texts(examples):
    concatenated_examples = {k: sum(examples[k], []) for k in examples.keys()}
    total_length = len(concatenated_examples[list(examples.keys())[0]])
    total_length = (total_length // block_size) * block_size
    result = {
        k: [t[i : i + block_size] for i in range(0, total_length, block_size)]
        for k, t in concatenated_examples.items()
    }
    result["labels"] = result["input_ids"].copy()
    return result

In [11]:
lm_dataset = tokenized_monthly_comments.map(group_texts, batched=True, num_proc=4)

#1:   0%|                                                                                                                                                                                                              | 0/12 [00:00<?, ?ba/s]

#2:   0%|                                                                                                                                                                                                              | 0/12 [00:00<?, ?ba/s]


#1:   8%|████████████████▌                                                                                                                                                                                     | 1/12 [00:01<00:17,  1.57s/ba]

#2:   8%|████████████████▌                                                                                                                                                                                     | 1/12 [00:01<00:15,  1.43s/ba]


#0:  17%|█████████████████████████████

#0: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 12/12 [00:17<00:00,  1.42s/ba]

#1:  92%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▌                | 11/12 [00:17<00:01,  1.56s/ba]

#2:  92%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▌                | 11/12 [00:17<00:01,  1.58s/ba]


#1:   0%|                                                                                                                                                                                                               | 0/3 [00:00<?, ?ba/s]

#2:   0%|                              

In [12]:
lm_dataset

DatasetDict({
    train: Dataset({
        features: ['input_ids', 'attention_mask', 'labels'],
        num_rows: 31858
    })
    test: Dataset({
        features: ['input_ids', 'attention_mask', 'labels'],
        num_rows: 8094
    })
})

In [13]:
from transformers import DataCollatorForLanguageModeling

tokenizer.pad_token = tokenizer.eos_token
data_collator = DataCollatorForLanguageModeling(tokenizer=tokenizer, mlm=False)

# Finetune

In [ ]:
model = AutoModelForCausalLM.from_pretrained(model_name).to(device_name)

In [55]:
training_args = TrainingArguments(
    output_dir=f"./models/{model_name}_{subreddit}_{month}",
    num_train_epochs=10,
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    weight_decay=0.01,
    logging_dir='./logs',  # directory for storing logs
    logging_steps=10,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=lm_dataset["train"],
    eval_dataset=lm_dataset["test"],
    data_collator=data_collator,
)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).


In [56]:
trainer.train()

/home/aww66/.conda/envs/huggingface/lib/python3.9/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 4836
  Num Epochs = 10
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 1
  Total optimization steps = 6050
  Number of trainable parameters = 81912576


Saving model checkpoint to ./models/distilgpt2_Judaism_2016-12/checkpoint-500
Configuration saved in ./models/distilgpt2_Judaism_2016-12/checkpoint-500/config.json
Model weights saved in ./models/distilgpt2_Judaism_2016-12/checkpoint-500/pytorch_model.bin
***** Running Evaluation *****
  Num examples = 1251
  Batch size = 8
Saving model checkpoint to ./models/distilgpt2_Judaism_2016-12/checkpoint-1000
Configuration saved in ./models/distilgpt2_Judaism_2016-12/checkpoint-1000/config.json
Model weights saved in ./models/distilgpt2_Judaism_2016-12/checkpoint-1000/pytorch_model.bin
***** Running Evaluation *****
  Num examples = 1251
  Batch size = 8
Saving model checkpoint to ./models/distilgpt2_Judaism_2016-12/checkpoint-1500
Configuration saved in ./models/distilgpt2_Judaism_2016-12/checkpoint-1500/config.json
Model weights saved in ./models/distilgpt2_Judaism_2016-12/checkpoint-1500/pytorch_model.bin
***** Running Evaluation *****
  Num examples = 1251
  Batch size = 8
Saving model che

TrainOutput(global_step=6050, training_loss=3.5959679154325124, metrics={'train_runtime': 583.9894, 'train_samples_per_second': 82.81, 'train_steps_per_second': 10.36, 'total_flos': 1579538857328640.0, 'train_loss': 3.5959679154325124, 'epoch': 10.0})

In [57]:
import math

eval_results = trainer.evaluate()
print(eval_results)
print(f"Perplexity: {math.exp(eval_results['eval_loss']):.2f}")

***** Running Evaluation *****
  Num examples = 1251
  Batch size = 8


Perplexity: 44.28


In [ ]:
# tokenizer.save_pretrained("./models/distilgpt2_Judaism_2016-12/checkpoint-6000/")

loading configuration file ./models/distilgpt2_Christianity_2016-12/checkpoint-10800/config.json
Model config GPT2Config {
  "_name_or_path": "./models/distilgpt2_Christianity_2016-12/checkpoint-10800",
  "_num_labels": 1,
  "activation_function": "gelu_new",
  "architectures": [
    "GPT2LMHeadModel"
  ],
  "attn_pdrop": 0.1,
  "bos_token_id": 50256,
  "embd_pdrop": 0.1,
  "eos_token_id": 50256,
  "id2label": {
    "0": "LABEL_0"
  },
  "initializer_range": 0.02,
  "label2id": {
    "LABEL_0": 0
  },
  "layer_norm_epsilon": 1e-05,
  "model_type": "gpt2",
  "n_ctx": 1024,
  "n_embd": 768,
  "n_head": 12,
  "n_inner": null,
  "n_layer": 6,
  "n_positions": 1024,
  "reorder_and_upcast_attn": false,
  "resid_pdrop": 0.1,
  "scale_attn_by_inverse_layer_idx": false,
  "scale_attn_weights": true,
  "summary_activation": null,
  "summary_first_dropout": 0.1,
  "summary_proj_to_labels": true,
  "summary_type": "cls_index",
  "summary_use_proj": true,
  "task_specific_params": {
    "text-gener

## Load model to evaluate

In [22]:
model = AutoModelForCausalLM.from_pretrained("./models/distilgpt2_Christianity_2016-12/best").to(device_name)

loading configuration file ./models/distilgpt2_Christianity_2016-12/best/config.json
Model config GPT2Config {
  "_name_or_path": "./models/distilgpt2_Christianity_2016-12/best",
  "_num_labels": 1,
  "activation_function": "gelu_new",
  "architectures": [
    "GPT2LMHeadModel"
  ],
  "attn_pdrop": 0.1,
  "bos_token_id": 50256,
  "embd_pdrop": 0.1,
  "eos_token_id": 50256,
  "id2label": {
    "0": "LABEL_0"
  },
  "initializer_range": 0.02,
  "label2id": {
    "LABEL_0": 0
  },
  "layer_norm_epsilon": 1e-05,
  "model_type": "gpt2",
  "n_ctx": 1024,
  "n_embd": 768,
  "n_head": 12,
  "n_inner": null,
  "n_layer": 6,
  "n_positions": 1024,
  "reorder_and_upcast_attn": false,
  "resid_pdrop": 0.1,
  "scale_attn_by_inverse_layer_idx": false,
  "scale_attn_weights": true,
  "summary_activation": null,
  "summary_first_dropout": 0.1,
  "summary_proj_to_labels": true,
  "summary_type": "cls_index",
  "summary_use_proj": true,
  "task_specific_params": {
    "text-generation": {
      "do_samp

In [23]:
training_args = TrainingArguments(
    output_dir="results/",
    num_train_epochs=10,
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    weight_decay=0.01,
    logging_dir='./logs',  # directory for storing logs
    logging_steps=10,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=lm_dataset["train"],
    eval_dataset=lm_dataset["test"],
    data_collator=data_collator,
)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).


In [24]:
trainer.evaluate()

***** Running Evaluation *****
  Num examples = 8094
  Batch size = 8


{'eval_loss': 3.3711485862731934,
 'eval_runtime': 14.9132,
 'eval_samples_per_second': 542.741,
 'eval_steps_per_second': 67.859}

# Inference / Evaluation

In [8]:
# https://huggingface.co/docs/transformers/perplexity
import torch
from tqdm import tqdm

def calculate_ppl(encodings):
    max_length = model.config.n_positions
    stride = 16
    seq_len = encodings.input_ids.size(1)

    nlls = []
    prev_end_loc = 0
    for begin_loc in tqdm(range(0, seq_len, stride)):
        end_loc = min(begin_loc + max_length, seq_len)
        trg_len = end_loc - prev_end_loc  # may be different from stride on last loop
        input_ids = encodings.input_ids[:, begin_loc:end_loc].to(device_name)
        target_ids = input_ids.clone()
        target_ids[:, :-trg_len] = -100

        with torch.no_grad():
            outputs = model(input_ids, labels=target_ids)

            # loss is calculated using CrossEntropyLoss which averages over input tokens.
            # Multiply it with trg_len to get the summation instead of average.
            # We will take average over all the tokens to get the true average
            # in the last step of this example.
            neg_log_likelihood = outputs.loss * trg_len

        nlls.append(neg_log_likelihood)

        prev_end_loc = end_loc
        if end_loc == seq_len:
            break

    ppl = torch.exp(torch.stack(nlls).sum() / end_loc)
    return ppl

In [9]:
checkpoint_path = "./models/distilgpt2_Judaism_2016-12/checkpoint-6000/"

In [10]:
inference_month = "2017-01"
input_texts = [t for t in 
               comments_df[comments_df['year-month'] == inference_month]['text']
               if t != ""]

model = AutoModelForCausalLM.from_pretrained(checkpoint_path).to(device_name)
tokenizer = AutoTokenizer.from_pretrained(checkpoint_path)
results = {"perplexities": list(), "mean_perplexity": None}
for text in input_texts:
    print(text)
    encodings = tokenizer(text, truncation=True, padding=True, return_tensors="pt")
    ppl = calculate_ppl(encodings)
    results['perplexities'].append(ppl.tolist())

The reason he specifies killed is because moshiach is a political and military leader, not a rabbi. 


  0%|                                                                                                                                                                                       | 0/2 [00:00<?, ?it/s]


This made me laugh more than it should have


  0%|                                                                                                                                                                                       | 0/1 [00:00<?, ?it/s]


Should I blame my phone like everyone else does, or just admit that I'm too lazy to proofread? 


...

&gt;I have met a lot of Muslims that have been condescending towards me and my religion, I'm not lying about that.

I don't doubt it.  There are 1.6 billion of us, there are definitely bad ones.  But next time don't smear an entire group based upon a bad experience, and I will acknowledge your experience in a more humane manner.

&gt;I also know that Muhammad basically killed every Jew he ever met for the most part.

I would debate that one.

&gt;Sorry for getting upset.

Honestly I owe you an apology.  I should have tried to understand you before getting offended and defensive, so I must apologize.  All I can tell you is that if it was me talking to you, I would do my best not to be a condescending jerk, and I am sorry the Muslims you encountered did not live their faith in their interpersonal interactions.


  0%|                                                                                                                                                                                      | 0/13 [00:00<?, ?it/s]


Truth.  The number of times I have had to straight up yell at idiot posters who repeat the dumbest stuff about Jews or Israel over at /r/Islam.  Luckily the mods seem to be picking it up better.


  0%|                                                                                                                                                                                       | 0/3 [00:00<?, ?it/s]


NameError: name 'np' is not defined

In [12]:
import numpy as np
np.mean(results['perplexities'])

95.95205189559745

In [29]:
results

{'perplexities': [57.758670806884766,
  27.13747787475586,
  67.93058013916016,
  25.875520706176758,
  82.38542175292969],
 'mean_perplexity': 52.21753425598145}

In [14]:
max_length = model.config.n_positions

In [15]:
max_length

1024

In [16]:
perplexity = evaluate.load("perplexity", module_type="metric")
MONTHS = [
    '2017-01', '2017-02', '2017-03', '2017-04', '2017-05', '2017-06', '2017-07', '2017-08',
    '2017-09', '2017-10', '2017-11', '2017-12'
         ]
ppl_results = dict()
for month in ['2017-02']
    print(month)
    input_texts = [t[:max_length] for t in 
                   comments_df[comments_df['year-month'] == month]['text']
                   if t != ""]
    ppl_results[month] = perplexity.compute(
        model_id='./models/distilgpt2_Judaism_2016-12/checkpoint-6000',
    #     model_id = 'distilgpt2',
        predictions = input_texts
    )

2017-01


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 772/772 [05:34<00:00,  2.31it/s]


2017-02


Token indices sequence length is longer than the specified maximum sequence length for this model (1118 > 1024). Running this sequence through the model will result in indexing errors
  0%|                                                                                                                                                                                     | 0/599 [00:00<?, ?it/s]../aten/src/ATen/native/cuda/Indexing.cu:1141: indexSelectLargeIndex: block: [43,0,0], thread: [0,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
../aten/src/ATen/native/cuda/Indexing.cu:1141: indexSelectLargeIndex: block: [43,0,0], thread: [1,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
../aten/src/ATen/native/cuda/Indexing.cu:1141: indexSelectLargeIndex: block: [43,0,0], thread: [2,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
../aten/src/ATen/native/cuda/Indexing.cu:1141: indexSelectLargeIndex: block: [43,0,0], thread: [3,0,0] Assertion `srcIndex < srcSelectDimSize` failed.
..

  0%|                                                                                                                                                                                     | 0/599 [00:00<?, ?it/s]


RuntimeError: The size of tensor a (1024) must match the size of tensor b (1119) at non-singleton dimension 3

In [19]:
np.mean(ppl_results['2017-01']['perplexities'])

92.03733834285907